In [1]:
import sys
import os
sys.path.insert(0, '../verificator')

In [2]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"

In [3]:
video_path = '/home/shareduser/d_test/data/videos/cam_2'
img_saving_path = '/home/shareduser/d_test/data/pics/cam_2_thr_0.5'
emb_saving_path ='/home/shareduser/d_test/data/models/embeddings'
numpy_saving_path = os.path.join(img_saving_path, 'deep_sort_features')

In [4]:
build_path = '/home/shareduser/d_test/data/models/yolo_init_config'
weights = os.path.join(build_path, 'bin', 'yolo.weights')
model = os.path.join(build_path, 'cfg', 'yolo-people.cfg')
cfg = os.path.join(build_path, 'cfg')
labels = os.path.join(build_path, 'labels.txt')
trained_model_path = '/home/shareduser/d_test/data/models/darkflow_retrain_all_imgs/full_data'

In [5]:
import numpy as np

In [6]:
from verificator.verificator import Verificator

In [7]:
from verificator.feature_extractor import DeepSortExtractor

In [8]:
deep_sort_model_path = '../verificator/verificator/deep_sort/resources/networks/mars-small128.ckpt-68577'

In [9]:
import tensorflow as tf

In [10]:
tf.reset_default_graph()
encoder = DeepSortExtractor(deep_sort_model_path)

feature dimensionality:  128


In [10]:
import cv2
img = '../../data/pics/persons_yolo_test/1/1_0.jpg'
img_ary = cv2.imread(img)

#img_ary = img_ary[np.newaxis]
img_ary.shape

(169, 84, 3)

In [11]:
features = encoder.encode(img_ary)
features.shape

(1, 128)

In [6]:
from verificator.tpe_predictor import TPEPredictor

Using TensorFlow backend.


In [13]:
model_saving_path = '../../data/models/tpe_weights'
model_saving_name = 'run_10_epochs.h5'

In [14]:
predictor = TPEPredictor(128,128)

../verificator/verificator/tpe_model/tpe_model_builder.py:43: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(128, input_dim=128, activation="linear", weights=[array([[ ..., use_bias=False)`
  base_model.add(Dense(n_out, input_dim=n_in, bias=False, weights=[W_pca], activation='linear'))
../verificator/verificator/tpe_model/tpe_model_builder.py:49: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  e = merge([a_emb, p_emb, n_emb], mode=triplet_merge, output_shape=triplet_merge_shape)
/home/shareduser/.local/lib/python3.5/site-packages/keras/legacy/layers.py:460: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
../verificator/verificator/tpe_model/tpe_model_builder.py:50: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outpu

In [15]:
predictor.load_weights(os.path.join(model_saving_path, model_saving_name))

In [16]:
predictor.weights_loaded

True

In [17]:
img1 = '../../data/pics/persons_yolo_test/1/1_0.jpg'
img2 = '../../data/pics/persons_yolo_test/2/2_0.jpg'
distance = 0.30296179983350968

In [18]:
v = Verificator(encoder, predictor)

In [19]:
v.verify(img1,img2,distance)

(array([[False]], dtype=bool), array([[ 0.12595434]], dtype=float32))

## Проверка детектора на видео cam 2

In [18]:
'''
def detect_and_save(self, tracker, encoder=None, tpe_predictor=None, save_mode='images', show_ids=True, verbose = True, video_file_path='', img_saving_path='',
embs_saving_path=None, emb_dump_size=1000, max_imgs_per_person=50, delay=1, show_video=False)
'''

"\ndef detect_and_save(self, tracker, encoder=None, tpe_predictor=None, save_mode='images', show_ids=True, verbose = True, video_file_path='', img_saving_path='',\nembs_saving_path=None, emb_dump_size=1000, max_imgs_per_person=50, delay=1, show_video=False)\n"

In [21]:
# опции детектора
options=dict()
options['model'] = model
options['load'] = -1
options['config'] = cfg
options['labels'] = labels
options['gpu'] = 0.8
options['threshold'] = 0.5
options['backup'] = os.path.join(trained_model_path, 'ckpt')
options['summary'] = os.path.join(trained_model_path, 'summary')

In [22]:
from verificator.detector import Detector

In [23]:
detector = Detector(options)

Parsing /home/shareduser/d_test/data/models/yolo_init_config/cfg/yolo-people.cfg
Loading None ...
Finished in 0.00011348724365234375s

Building net ...
Source | Train? | Layer description                | Output size
-------+--------+----------------------------------+---------------
       |        | input                            | (?, 608, 608, 3)
 Init  |  Yep!  | conv 3x3p1_1  +bnorm  leaky      | (?, 608, 608, 32)
 Load  |  Yep!  | maxp 2x2p0_2                     | (?, 304, 304, 32)
 Init  |  Yep!  | conv 3x3p1_1  +bnorm  leaky      | (?, 304, 304, 64)
 Load  |  Yep!  | maxp 2x2p0_2                     | (?, 152, 152, 64)
 Init  |  Yep!  | conv 3x3p1_1  +bnorm  leaky      | (?, 152, 152, 128)
 Init  |  Yep!  | conv 1x1p0_1  +bnorm  leaky      | (?, 152, 152, 64)
 Init  |  Yep!  | conv 3x3p1_1  +bnorm  leaky      | (?, 152, 152, 128)
 Load  |  Yep!  | maxp 2x2p0_2                     | (?, 76, 76, 128)
 Init  |  Yep!  | conv 3x3p1_1  +bnorm  leaky      | (?, 76, 76, 256)
 Init 

In [24]:
from sort.sort import Sort

In [25]:
tracker = Sort()

In [26]:
'''
detector.detect_and_save(
    tracker,encoder=encoder,
    tpe_predictor=predictor,
    save_mode='all',
    video_file_path=video_path,
    img_saving_path=img_saving_path,
    embs_saving_path=emb_saving_path,
    show_video=False)
'''

"\ndetector.detect_and_save(\n    tracker,encoder=encoder,\n    tpe_predictor=predictor,\n    save_mode='all',\n    video_file_path=video_path,\n    img_saving_path=img_saving_path,\n    embs_saving_path=emb_saving_path,\n    show_video=False)\n"

### --проверили, работает---

## Проверка обучения tpe-верификатора

In [7]:
from verificator.feature_extractor import *

In [6]:
import tensorflow as tf

In [7]:
tf.reset_default_graph()

In [14]:
fextractor = DeepSortExtractor(deep_sort_model_path)

feature dimensionality:  128


In [8]:
#from verificator.utils.clean_after_detections import clean_dirs, rename_folders, move_files_to_test_dir_for_verificator

In [18]:
cam_1_train = os.path.expanduser('~/d_test/data/pics/final_sets/clean_cam_1_thr_0.5/train')
cam_2_train = os.path.expanduser('~/d_test/data/pics/final_sets/clean_cam_2_thr_0.5/train')
cam_1_2_train = os.path.expanduser('~/d_test/data/pics/final_sets/cam_1_2/train')

In [27]:
labels, features = fextractor.encode_from_dirs(cam_1_2_train)

In [28]:
features.shape

(23202, 128)

In [22]:
cam_1_features= os.path.expanduser('~/d_test/data/models/final_models/features/cam_1')
cam_2_features = os.path.expanduser('~/d_test/data/models/final_models/features/cam_2')
cam_1_2_features = os.path.expanduser('~/d_test/data/models/final_models/features/cam_1_2')

In [29]:
# сохранили фичи, созданные в deep sort 
np.save(os.path.join(cam_1_2_features, 'cam_1_2_features.npy'), features)
np.save(os.path.join(cam_1_2_features, 'cam_1_2_labels.npy'), labels)

In [32]:
pred_to_train = TPEPredictor(128,128)

../verificator/verificator/tpe_model/tpe_model_builder.py:43: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(128, weights=[array([[ ..., use_bias=False, activation="linear", input_dim=128)`
  base_model.add(Dense(n_out, input_dim=n_in, bias=False, weights=[W_pca], activation='linear'))
../verificator/verificator/tpe_model/tpe_model_builder.py:49: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  e = merge([a_emb, p_emb, n_emb], mode=triplet_merge, output_shape=triplet_merge_shape)
/home/shareduser/.local/lib/python3.5/site-packages/keras/legacy/layers.py:460: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
../verificator/verificator/tpe_model/tpe_model_builder.py:50: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outpu

In [33]:
tpe_1_saving_path = os.path.expanduser('~/d_test/data/models/final_models/weights/cam_1')
tpe_1_2_saving_path = os.path.expanduser('~/d_test/data/models/final_models/weights/cam_1_2')

In [34]:
features = np.load(os.path.join(cam_1_features, 'cam_1_features.npy'))
labels = np.load(os.path.join(cam_1_features, 'cam_1_labels.npy'))

In [35]:
features.shape

(19447, 128)

In [36]:
mineer, mindeer = pred_to_train.train(
    20, 32, weights_saving_path=tpe_1_saving_path, weights_saving_name='cam_1_20_epoch_deep_sort_features.h5',
    labels=labels, embeddings=features)

training tpe, number of train data (15921, 128), number of dev data (3525, 128), epochs 20
epoch: 0
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.8023
min score: -0.23228856921195984, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7571
min score: -0.18338963389396667, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7386
min score: -0.17127485573291779, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7367
min score: -0.1606178879737854, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7011
min score: -0.1600421965122223, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7030
min score: -0.15212495625019073, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7003
min score: -0.15330037474632263, max scor

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6631
min score: -0.33237549662590027, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6644
min score: -0.3422738313674927, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6762
min score: -0.36672115325927734, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7150
min score: -0.3609273135662079, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6921
min score: -0.366890013217926, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6906
min score: -0.3683740496635437, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6674
min score: -0.3914645314216614, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6633
min score: -0

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7107
min score: -0.49003997445106506, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6864
min score: -0.4987545311450958, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6542
min score: -0.5121687054634094, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6822
min score: -0.5199170708656311, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6917
min score: -0.5162721872329712, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6837
min score: -0.5232765078544617, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7110
min score: -0.5162990093231201, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6708
min score: -0

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6902
min score: -0.4988848865032196, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6599
min score: -0.5180415511131287, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6928
min score: -0.5182228684425354, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7146
min score: -0.5070736408233643, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6874
min score: -0.5101094841957092, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6800
min score: -0.5214105248451233, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7019
min score: -0.5292348265647888, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6651
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6846
min score: -0.5440619587898254, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6724
min score: -0.5527340769767761, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7032
min score: -0.54428631067276, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7151
min score: -0.5322652459144592, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6937
min score: -0.5243873596191406, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6856
min score: -0.5281717777252197, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6816
min score: -0.5427009463310242, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7033
min score: -0.51

...

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6943
min score: -0.6079593300819397, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6778
min score: -0.61202472448349, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6945
min score: -0.6086923480033875, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6862
min score: -0.6081627607345581, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6637
min score: -0.5993695855140686, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6611
min score: -0.6013162136077881, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7055
min score: -0.5892168879508972, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6503
min score: -0.58

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6625
min score: -0.6029659509658813, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6483
min score: -0.6082949042320251, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6730
min score: -0.6124752759933472, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6976
min score: -0.6132532954216003, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6771
min score: -0.6220163702964783, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7002
min score: -0.6210862398147583, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6726
min score: -0.6239311695098877, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6631
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6660
min score: -0.6069507598876953, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6652
min score: -0.6084945201873779, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6728
min score: -0.608570396900177, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6861
min score: -0.6128512620925903, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6671
min score: -0.622189998626709, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6936
min score: -0.5982999205589294, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6722
min score: -0.601803719997406, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6790
min score: -0.612

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6544
min score: -0.593810498714447, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6720
min score: -0.6015031933784485, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6699
min score: -0.6120634078979492, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6742
min score: -0.5992947220802307, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7120
min score: -0.5843049883842468, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6749
min score: -0.584064781665802, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6399
min score: -0.5960860252380371, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6466
min score: -0.61

KeyboardInterrupt: 

In [37]:
pred_to_train.model.save_weights(os.path.join(tpe_1_saving_path, 'cam_1_deep_sort_features_best.h5'))

In [12]:
tf.reset_default_graph()

In [8]:
inception_predictor = TPEPredictor(2048,512)

../verificator/verificator/tpe_model/tpe_model_builder.py:43: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(512, use_bias=False, activation="linear", input_dim=2048, weights=[array([[ ...)`
  base_model.add(Dense(n_out, input_dim=n_in, bias=False, weights=[W_pca], activation='linear'))
../verificator/verificator/tpe_model/tpe_model_builder.py:49: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  e = merge([a_emb, p_emb, n_emb], mode=triplet_merge, output_shape=triplet_merge_shape)
/home/shareduser/.local/lib/python3.5/site-packages/keras/legacy/layers.py:460: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
../verificator/verificator/tpe_model/tpe_model_builder.py:50: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inpu

In [9]:
inc_feat_1 = os.path.expanduser('~/d_test/data/models/final_models/features/inception_features/cam_1')
inc_feat_1_2 = os.path.expanduser('~/d_test/data/models/final_models/features/inception_features/cam_1_2')

In [10]:
features = np.load(os.path.join(inc_feat_1, 'cam_1_inception_features.npy'))
labels = np.load(os.path.join(inc_feat_1, 'cam_1_inception_labels.npy'))

In [11]:
w_saving_path_1 = os.path.expanduser('~/d_test/data/models/final_models/weights/inception/cam_1')
w_saving_path_1_2 = os.path.expanduser('~/d_test/data/models/final_models/weights/inception/cam_1_2')

In [12]:
mineer_inc, mindeer_inc = inception_predictor.train(
    20, 32, save_weights=True, weights_saving_path=w_saving_path_1, weights_saving_name='cam_1_20_epoch_inception_features.h5',
    labels=labels, embeddings=features)

training tpe, number of train data (15921, 2048), number of dev data (3525, 2048), epochs 20
save_weights True
epoch: 0
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6851
min score: 0.40865564346313477, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6904
min score: 0.3978363275527954, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6985
min score: 0.5212850570678711, max score: 1.0000011920928955
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6795
min score: 0.22686317563056946, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6894
min score: 0.28934669494628906, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6803
min score: 0.16841287910938263, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6878
min score: 0.2454963028430938

32/32 [==============================] - 0s - loss: 0.6529
min score: -0.4186408221721649, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6800
min score: -0.2146061509847641, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6722
min score: -0.28458160161972046, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6713
min score: -0.334026575088501, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6559
min score: -0.35606133937835693, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6710
min score: -0.19885234534740448, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6606
min score: -0.3577001690864563, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.7050
min score: -0.12750332

32/32 [==============================] - 0s - loss: 0.6573
min score: -0.37394654750823975, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6351
min score: -0.41118913888931274, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6706
min score: -0.37948930263519287, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6414
min score: -0.3916671872138977, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6598
min score: -0.32969218492507935, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6416
min score: -0.44365194439888, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6527
min score: -0.3792381286621094, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6505
min score: -0.41833084

32/32 [==============================] - 0s - loss: 0.6633
min score: -0.40606656670570374, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6568
min score: -0.40236905217170715, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6441
min score: -0.4712343215942383, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6736
min score: -0.3108116090297699, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6413
min score: -0.5081918239593506, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6475
min score: -0.3995441794395447, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6372
min score: -0.5146799087524414, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6552
min score: -0.398354917

32/32 [==============================] - 0s - loss: 0.6673
min score: -0.39191725850105286, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6443
min score: -0.5013907551765442, max score: 1.0000008344650269
EER: 8.95
weights /home/shareduser/d_test/data/models/final_models/weights/inception/cam_1/cam_1_20_epoch_inception_features_0.h5 saved
epoch: 1
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6390
min score: -0.47882941365242004, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6361
min score: -0.5194157958030701, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6739
min score: -0.35304197669029236, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6397
min score: -0.552893340587616, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6462
min scor

...

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6045
min score: -0.5668478012084961, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6128
min score: -0.5410871505737305, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5946
min score: -0.5575827360153198, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5967
min score: -0.5952869057655334, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5867
min score: -0.6111906170845032, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5889
min score: -0.5645897388458252, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5831
min score: -0.5452975034713745, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5891
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5649
min score: -0.5459660291671753, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5933
min score: -0.5662553310394287, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5612
min score: -0.6204199194908142, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5859
min score: -0.5520905256271362, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5784
min score: -0.6006456613540649, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5984
min score: -0.5999057292938232, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5841
min score: -0.5862404108047485, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5767
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5968
min score: -0.5808457732200623, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5912
min score: -0.5762017965316772, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5904
min score: -0.5278559923171997, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5882
min score: -0.5595013499259949, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6066
min score: -0.5842797160148621, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5863
min score: -0.5533863306045532, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5644
min score: -0.5263648629188538, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5954
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5903
min score: -0.556405246257782, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5895
min score: -0.5548975467681885, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5971
min score: -0.562565803527832, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5808
min score: -0.5856233239173889, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5983
min score: -0.5717083215713501, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5866
min score: -0.5735102891921997, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5927
min score: -0.5432478189468384, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5770
min score: -0.55

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5823
min score: -0.5469411611557007, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5832
min score: -0.5633814930915833, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5978
min score: -0.577614426612854, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5957
min score: -0.581545889377594, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5857
min score: -0.5940849781036377, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5836
min score: -0.5667412281036377, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5938
min score: -0.5463047623634338, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5930
min score: -0.50

In [14]:
inception_predictor.model.save_weights('/home/shareduser/d_test/data/models/final_models/weights/inception/cam_1/cam_1_best.h5')

In [15]:
tf.reset_default_graph()

In [16]:
features_1_2 = np.load(os.path.join(inc_feat_1_2, 'cam_1_2_inception_features.npy'))
labels_1_2 = np.load(os.path.join(inc_feat_1_2, 'cam_1_2_inception_labels.npy'))

In [17]:
mineer_inc_2, mindeer_inc_2 = inception_predictor.train(
    20, 32, save_weights=True, weights_saving_path=w_saving_path_1_2, weights_saving_name='cam_1_2_20_epoch_inception_features.h5',
    labels=labels_1_2, embeddings=features_1_2)

training tpe, number of train data (19011, 2048), number of dev data (4190, 2048), epochs 20
save_weights True
epoch: 0
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6901
min score: 0.4217374324798584, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6722
min score: 0.25937527418136597, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6957
min score: 0.3109157979488373, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6753
min score: 0.18929725885391235, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6786
min score: 0.13606233894824982, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6922
min score: 0.14346975088119507, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6975
min score: 0.27728816866874695,

32/32 [==============================] - 0s - loss: 0.6539
min score: -0.3879261612892151, max score: 1.0000011920928955
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6664
min score: -0.2745327949523926, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6846
min score: -0.18479226529598236, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6597
min score: -0.40518102049827576, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6750
min score: -0.1910158395767212, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6500
min score: -0.39620643854141235, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6629
min score: -0.21552884578704834, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6422
min score: -0.3774412

32/32 [==============================] - 0s - loss: 0.6452
min score: -0.4049544632434845, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6814
min score: -0.22414974868297577, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6745
min score: -0.31437772512435913, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6735
min score: -0.3076435327529907, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6402
min score: -0.3728974461555481, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6491
min score: -0.29374054074287415, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6855
min score: -0.2336166501045227, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6623
min score: -0.3607225

32/32 [==============================] - 0s - loss: 0.6539
min score: -0.49039095640182495, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6846
min score: -0.2996978163719177, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6711
min score: -0.39672088623046875, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6544
min score: -0.44214147329330444, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6525
min score: -0.3605542778968811, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6461
min score: -0.4240947961807251, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6654
min score: -0.4258463382720947, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6512
min score: -0.4362095

32/32 [==============================] - 0s - loss: 0.6620
min score: -0.3785138726234436, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6497
min score: -0.4692551791667938, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6697
min score: -0.383516788482666, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6293
min score: -0.5014203786849976, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6458
min score: -0.3987696170806885, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6559
min score: -0.4514757990837097, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6469
min score: -0.4733046293258667, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6529
min score: -0.512075901031

...

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5829
min score: -0.5972654223442078, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5843
min score: -0.5712313055992126, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5891
min score: -0.5563050508499146, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5856
min score: -0.558427095413208, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5756
min score: -0.5550116300582886, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5922
min score: -0.6139244437217712, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6200
min score: -0.5262412428855896, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5974
min score: -0.5

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5891
min score: -0.5560439229011536, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5819
min score: -0.5662063360214233, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5778
min score: -0.5920240879058838, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5682
min score: -0.5726860761642456, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5769
min score: -0.5595505237579346, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5950
min score: -0.5639587044715881, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5868
min score: -0.5996356010437012, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5953
min score: -0.

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5968
min score: -0.5447808504104614, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5836
min score: -0.5732153058052063, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5973
min score: -0.5949998497962952, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5917
min score: -0.5215854644775391, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6019
min score: -0.5612586140632629, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6032
min score: -0.5717962980270386, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5928
min score: -0.555795431137085, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5890
min score: -0.5

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5889
min score: -0.5569772720336914, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5762
min score: -0.5728472471237183, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5788
min score: -0.5844886898994446, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5939
min score: -0.5633584856987, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6047
min score: -0.6037547588348389, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6148
min score: -0.5337443947792053, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5915
min score: -0.5915837287902832, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5962
min score: -0.553

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6024
min score: -0.5786206722259521, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6007
min score: -0.5920581221580505, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5965
min score: -0.5442345142364502, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6053
min score: -0.5845034122467041, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5872
min score: -0.557703971862793, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5718
min score: -0.5389426350593567, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5997
min score: -0.5626287460327148, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5665
min score: -0.5

In [18]:
inception_predictor.model.save_weights(os.path.join(w_saving_path_1_2, 'cam_1_2_best_weights.h5'))

In [21]:
with open(os.path.join(w_saving_path_1_2, 'deer.txt'), 'w') as f:
    f.write(str(mindeer_inc_2))

In [23]:
exclude_indices = np.random.choice(709, 50, replace=False)

In [25]:
w_saving_path_50_excl = os.path.expanduser('~/d_test/data/models/final_models/weights/inception/cam_1_2_50_excluded')

In [26]:
with open(os.path.join(w_saving_path_50_excl, 'excluded_labels.txt'), 'w') as f:
    f.write(str(exclude_indices))

In [120]:
with open(os.path.join(w_saving_path_50_excl, 'excluded_labels.txt'), 'r') as f:
    e_l = f.read()

In [122]:
np.save(os.path.join(w_saving_path_50_excl, 'excluded_labels.npy'), exclude_indices)

In [124]:
e_i = np.load(os.path.join(w_saving_path_50_excl, 'excluded_labels.npy'))
e_i

array([442,  85, 403, 305, 272, 308, 583, 155, 201, 159, 476, 127, 211,
        26,  72, 313, 170, 317, 420, 304, 675, 158, 513, 558, 523, 226,
       325, 674, 591, 125, 687, 323,   6,  48, 164, 230, 342, 549, 288,
       402, 516, 166,  19, 189, 379, 444, 561, 151, 581, 505])

In [38]:
labels_50 = labels_1_2
features_50 = features_1_2

In [57]:
features_1_2.shape

(23202, 2048)

In [39]:
for l in exclude_indices:
    new_indices = np.where(labels_50 != l)
    labels_50 = labels_50[new_indices]
    features_50 = features_50[new_indices]

In [40]:
labels_50.shape

(21372,)

In [42]:
features_50.shape

(21372, 2048)

In [43]:
tf.reset_default_graph()

In [44]:
mineer_inc_3, mindeer_inc_3 = inception_predictor.train(
    20, 32, save_weights=True, weights_saving_path=w_saving_path_50_excl, weights_saving_name='cam_1_2_50_excl_inception_features.h5',
    labels=labels_50, embeddings=features_50)

training tpe, number of train data (17515, 2048), number of dev data (3856, 2048), epochs 20
save_weights True
epoch: 0
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6801
min score: 0.35501521825790405, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6929
min score: 0.3759395182132721, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6866
min score: 0.3262645900249481, max score: 1.0000011920928955
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6791
min score: 0.24309462308883667, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6782
min score: 0.20082107186317444, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6756
min score: 0.10619606822729111, max score: 1.0000011920928955
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6739
min score: 0.0958578214049339

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6755
min score: -0.24222731590270996, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6817
min score: -0.16143524646759033, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6719
min score: -0.2448972761631012, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6655
min score: -0.23335108160972595, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6707
min score: -0.18626418709754944, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6651
min score: -0.2843470573425293, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6701
min score: -0.1896655261516571, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6651
min score: 

32/32 [==============================] - 0s - loss: 0.6751
min score: -0.3112114667892456, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6551
min score: -0.37581050395965576, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6643
min score: -0.350458562374115, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6814
min score: -0.30774185061454773, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6550
min score: -0.48639893531799316, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6468
min score: -0.3220234811306, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6651
min score: -0.36629578471183777, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6579
min score: -0.355550885200

32/32 [==============================] - 0s - loss: 0.6538
min score: -0.3762132525444031, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6697
min score: -0.37083107233047485, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6657
min score: -0.42154356837272644, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6615
min score: -0.38321417570114136, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6448
min score: -0.46135348081588745, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6529
min score: -0.4035291373729706, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6334
min score: -0.40011292695999146, max score: 1.0000009536743164
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6481
min score: -0.42734

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6530
min score: -0.41054898500442505, max score: 1.000001072883606
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6366
min score: -0.4789097309112549, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6516
min score: -0.4544781744480133, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6359
min score: -0.47552603483200073, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6486
min score: -0.46535563468933105, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6366
min score: -0.5172088742256165, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6314
min score: -0.4548354148864746, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6506
min score: -

...

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5832
min score: -0.5703716278076172, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5933
min score: -0.5684321522712708, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5938
min score: -0.5374075174331665, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5971
min score: -0.5745983123779297, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6032
min score: -0.5704167485237122, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5921
min score: -0.5900684595108032, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5818
min score: -0.621342658996582, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5834
min score: -0.6

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5909
min score: -0.5942250490188599, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6042
min score: -0.584345817565918, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6075
min score: -0.6231934428215027, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5695
min score: -0.5613588094711304, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6173
min score: -0.5502381920814514, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6167
min score: -0.6052024364471436, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5884
min score: -0.5925830006599426, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5871
min score: -0.6

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6106
min score: -0.5780574679374695, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5859
min score: -0.5650417804718018, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5942
min score: -0.5486822128295898, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6195
min score: -0.6059840321540833, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6068
min score: -0.618952751159668, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5806
min score: -0.5879056453704834, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5910
min score: -0.5778008699417114, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5866
min score: -0.5

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5859
min score: -0.5477489233016968, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5903
min score: -0.5651984214782715, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5723
min score: -0.5519231557846069, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5935
min score: -0.5614166259765625, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5791
min score: -0.575953483581543, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5683
min score: -0.5464198589324951, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6091
min score: -0.5545912981033325, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.6014
min score: -0.5

Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5731
min score: -0.619513750076294, max score: 1.0000005960464478
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5890
min score: -0.5772372484207153, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5881
min score: -0.563342809677124, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5999
min score: -0.5707442760467529, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5955
min score: -0.5447366237640381, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5717
min score: -0.5961073637008667, max score: 1.0000008344650269
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5903
min score: -0.5824535489082336, max score: 1.0000007152557373
Epoch 1/1
32/32 [==============================] - 0s - loss: 0.5803
min score: -0.55

In [45]:
inception_predictor.model.save_weights(os.path.join(w_saving_path_50_excl, 'ca_1_2_50_excl_best.h5'))

In [51]:
excluded_labels_50 = np.array([])
excluded_features_50 = None
for l in exclude_indices:
    new_indices = np.where(labels_1_2 == l)
    excluded_labels_50 = np.append(excluded_labels_50, labels_1_2[new_indices])
    if excluded_features_50 is None:
        excluded_features_50 = features_1_2[new_indices]
    else:
        excluded_features_50 = np.vstack([excluded_features_50, features_1_2[new_indices]])

In [54]:
excluded_features_50.shape

(1830, 2048)

In [55]:
tpe_excluded_features_50 = inception_predictor.predict(excluded_features_50)

In [58]:
tpe_features_50 = inception_predictor.predict(features_50)

In [146]:
tpe_threshold = 0.31419761975606286
in_class_threshold = 0.75
all_un_scores = None
all_pers_id = []
for label in np.unique(excluded_labels_50):
    unknown_person_features = tpe_excluded_features_50[np.where(excluded_labels_50 == label)]
    pers_identified = []
    for known_label in np.unique(labels_50):   # для каждой известной персоны
        known_person_features = tpe_features_50[np.where(labels_50 == known_label)]  # берем фичи этой персоны
        scores = unknown_person_features @ known_person_features.T >= tpe_threshold  # проводим идентификацию каждого изображения с каждым
        scores = np.sum(scores, axis=1)/scores.shape[1] >= in_class_threshold        # проверяем, идентифицировано ли изображение неизвестной персоны
        scores = np.sum(scores)/scores.shape[0] >= in_class_threshold                # проверяем, сколько изображений неизвестной персоны идентифицировано
        pers_identified.append(scores)
    # pers_identified - флаги идентификации неизвестного изображения с каждым  из известных классов
    all_pers_id.append(sum(pers_identified)) # если есть идентификации, то в итоговый результат попадет ненулевое значение 
print('FAR: {}'.format(len(np.nonzero(all_pers_id)[0])/len(all_pers_id))) # смотрим, сколько есть ненулевых значений из всех

tar_pers_id = []
for label in np.unique(excluded_labels_50):
    person_features = tpe_excluded_features_50[np.where(excluded_labels_50 == label)]
    scores = person_features @ person_features.T >= tpe_threshold
    scores = np.sum(scores, axis=1)/scores.shape[1] >= in_class_threshold
    scores = np.sum(scores)/scores.shape[0] >= in_class_threshold
    tar_pers_id.append(scores)
print('FRR: {}'.format(1-sum(tar_pers_id)/len(tar_pers_id)))

FAR: 0.24
FRR: 0.30000000000000004


In [95]:
len(np.nonzero(all_pers_id)[0])/len(all_pers_id)

0.2

In [142]:
# imposter- тест для неизвестных персон
tpe_threshold = 0.31419761975606286
in_class_threshold = 0.68
imp_pers_id = []
for label in np.unique(excluded_labels_50):
    person_features = tpe_excluded_features_50[np.where(excluded_labels_50 == label)]
    pers_identified = []
    for other_label in np.unique(excluded_labels_50[np.where(excluded_labels_50!=label)]):
        other_features = tpe_excluded_features_50[np.where(excluded_labels_50 == other_label)]
        scores = person_features @ other_features.T >= tpe_threshold
        scores = np.sum(scores, axis=1)/scores.shape[1] >= in_class_threshold
        scores = np.sum(scores)/scores.shape[0] >= in_class_threshold
        pers_identified.append(scores)
    imp_pers_id.append(sum(pers_identified))

tar_pers_id = []
for label in np.unique(excluded_labels_50):
    person_features = tpe_excluded_features_50[np.where(excluded_labels_50 == label)]
    scores = person_features @ person_features.T >= tpe_threshold
    scores = np.sum(scores, axis=1)/scores.shape[1] >= in_class_threshold
    scores = np.sum(scores)/scores.shape[0] >= in_class_threshold
    tar_pers_id.append(scores)


print('FAR: {}'.format(len(np.nonzero(imp_pers_id)[0])/len(imp_pers_id)))
print('FRR: {}'.format(1-sum(tar_pers_id)/len(tar_pers_id)))

FAR: 0.1
FRR: 0.12


In [133]:
# target-тест для неизвестных персон
tpe_threshold = 0.31419761975606286
in_class_threshold = 0.6
tar_pers_id = []
for label in np.unique(excluded_labels_50):
    person_features = tpe_excluded_features_50[np.where(excluded_labels_50 == label)]
    scores = person_features @ person_features.T >= tpe_threshold
    scores = np.sum(scores, axis=1)/scores.shape[1] >= in_class_threshold
    scores = np.sum(scores)/scores.shape[0] >= in_class_threshold
    tar_pers_id.append(scores)

print(sum(tar_pers_id)/len(tar_pers_id))
#     imp_pers_id.append(sum(pers_identified))
# print(len(np.nonzero(imp_pers_id)[0])/len(imp_pers_id))

1.0


In [109]:
imp_pers_id

{6.0: [False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False],
 19.0: [False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False],
 26.0: [False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
  False,
